In [282]:
import itertools
import numpy as np
import os
import seaborn as sns
from tqdm import tqdm
from dataclasses import asdict, dataclass, field
import vsketch
import shapely.geometry as sg
from shapely.geometry import box, MultiLineString, Point, MultiPoint, Polygon, MultiPolygon, LineString
import shapely.affinity as sa
import shapely.ops as so
import matplotlib.pyplot as plt
import pandas as pd

import vpype_cli
from typing import List, Generic
from genpen import genpen as gp, utils as utils
from scipy import stats as ss
import geopandas
from shapely.errors import TopologicalError
import functools
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [267]:
def occlude(top, bottom, distance=1e-6):
    try:
        return bottom.difference(top)
    except TopologicalError:
        return bottom.buffer(distance).difference(top.buffer(distance))

In [268]:
class ParticleCluster(object):
    
    def __init__(
        self,
        pos,
        perlin_grid,
    ):
        self.pos = Point(pos)
        self.pg = perlin_grid
        self.particles = []
        
    def gen_start_pts_gaussian(
            self,
            n_particles=10,
            xloc=0.,
            xscale=1.,
            yloc=0.,
            yscale=1.,
        ):
        xs = self.pos.x + ss.norm(loc=xloc, scale=xscale).rvs(n_particles)
        ys = self.pos.y + ss.norm(loc=yloc, scale=yscale).rvs(n_particles)
        self.start_pts = [Point((x,y)) for x,y in zip(xs, ys)]
        
    def init_particles(self, start_bounds=None):
        for pt in self.start_pts:
            p = gp.Particle(pos=pt, grid=self.pg)
            if start_bounds == None:
                self.particles.append(p)
            elif start_area.contains(p.pos):
                self.particles.append(p)
                
    @functools.singledispatchmethod           
    def step(self, n_steps):
        for p,n in zip(self.particles, n_steps):
            for i in range(n):
                p.step()
    
    @step.register
    def _(self, n_steps: int):
        n_steps = [n_steps] * len(self.particles)
        for p,n in zip(self.particles, n_steps):
                for i in range(n):
                    p.step()
                    
    @property
    def lines(self):
        return MultiLineString([p.line for p in self.particles])
    

In [269]:
@dataclass
class ScaleTransPrms(gp.DataClassBase):
    
    n_iters: int = 100
    d_buffer: float = -0.25
    d_translate_factor: float = 0.9
    d_translate: float = None
    angles: float = 0.
    d_translates: list = field(default=None, init=False)
    def __post_init__(self):
        self.d_buffers = np.array([self.d_buffer] * self.n_iters)
        
        if self.d_translates == None:
            if self.d_translate != None:
                self.d_translates =  np.array([self.d_translate] * self.n_iters)
            else:
                self.d_translates = self.d_buffers * self.d_translate_factor
    
    @property
    def prms(self):
        varnames = ['d_buffers', 'd_translates', 'angles']
        return {var: getattr(self, var) for var in varnames}

In [270]:
def individual_difference(multipolygon0, multipolygon1, dist=1e-6):
    diffs = []
    for p0, p1 in itertools.product(multipolygon0, multipolygon1):
        if p0.overlaps(p1):
            try:
                diff = p0.difference(p1)
            except TopologicalError:
                diff = p0.buffer(dist).difference(p1.buffer(dist))
            diffs.append(diff)
    return diffs

## try 1

In [200]:
page_x_inches: float = 11. # inches
page_y_inches: float = 8.5 # inches
border:float = 0.

perlin_grid_params = {
    'xstep':3,
    'ystep':3,
    'lod':10,
    'falloff':None,
    'noise_scale':0.0073,
    'noiseSeed':6
}

particle_init_grid_params = {
    'xstep':16,
    'ystep':16,
}

buffer_style = 2

In [3]:
px = utils.DistanceConverter(page_x_inches, 'inches').mm
py = utils.DistanceConverter(page_y_inches, 'inches').mm
page_format = f'{px}mmx{py}mm'
drawbox = sg.box(border, border, px-border, py-border)

xmin, ymin, xmax, ymax = drawbox.bounds
brad = np.min([gp.get_width(drawbox), gp.get_height(drawbox)])
pg = gp.PerlinGrid(drawbox, **perlin_grid_params)

In [4]:
start_area = sa.scale(drawbox.centroid.buffer(brad*0.45), xfact=1.3)

In [36]:
start_area = drawbox.buffer(-20)

In [63]:
xcs, ycs = gp.overlay_grid(start_area, xstep=19, ystep=15)
start_pts = [Point(x,y) for x,y in itertools.product(xcs, ycs)]
start_pts = [p for p in start_pts if start_area.contains(p)]

In [68]:
gpolys = []
for p in start_pts:

    pc = ParticleCluster(pos=p, perlin_grid=pg)
    pc.gen_start_pts_gaussian(n_particles=20, xscale=4, yscale=4)
    pc.init_particles()
    n_steps = np.random.randint(low=10, high=50, size=len(pc.particles))
    pc.step(n_steps)

    buffer_distances = np.random.uniform(low=0.3, high=1.3) + np.random.uniform(low=0., high=0.7, size=len(pc.lines))
    polys = []
    for line, bd in zip(pc.lines, buffer_distances):
        poly = line.buffer(bd,
            cap_style=buffer_style,
            join_style=buffer_style)
        polys.append(poly)

    P = gp.Poly(so.unary_union(polys))

    stp = ScaleTransPrms(
        d_buffer=np.random.uniform(low=-0.45, high=-0.25), 
        angles=-90,

    )
    stp.d_buffers += np.random.uniform(-0.03, 0.03, size=stp.d_buffers.shape)
    P.fill_scale_trans(**stp.prms)
    gpolys.append(P)

In [69]:
zorder = np.random.permutation(len(gpolys))

for z, gpoly in zip(zorder, gpolys):
    gpoly.z = z

for gp0, gp1 in itertools.combinations(gpolys, r=2):
    try:
        overlaps = gp0.p.overlaps(gp1.p)
    except :
        gp0.p = gp0.p.buffer(1e-6)
        gp1.p = gp1.p.buffer(1e-6)
        overlaps = gp0.p.overlaps(gp1.p)
    if overlaps:
        if gp0.z > gp1.z:
            gp1.p = occlude(top=gp0.p, bottom=gp1.p)
        elif gp0.z < gp1.z:
            gp0.p = occlude(top=gp1.p, bottom=gp0.p)

In [70]:
ifills = []
for p in gpolys:
    try:
        ifills.append(p.intersection_fill)
    except:
        pass

splits = utils.random_split(ifills, n_layers=5)
layers = [utils.merge_LineStrings(split) for split in splits]

In [ ]:
sk = vsketch.Vsketch()
sk.size(page_format)
sk.scale('1mm')
sk.penWidth('0.25mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)
sk.display(color_mode='layer')

In [72]:
savepath = '/mnt/c/code/side/plotter_images/oned_outputs/0083_perlin_flow_erode_frays_occlude.svg'

sk.save(savepath)

vpype_commands = 'linesimplify --tolerance 0.01mm linemerge --tolerance 0.1mm reloop linesort'
vpype_str = f'vpype read -q 0.05mm {savepath} {vpype_commands} write --page-format {page_format} {savepath}'

os.system(vpype_str)

512

## try 2

In [283]:
page_x_inches: float = 11. # inches
page_y_inches: float = 8.5 # inches
border:float = 0.

perlin_grid_params = {
    'xstep':1,
    'ystep':1,
    'lod':10,
    'falloff':None,
    'noise_scale':0.0073,
    'noiseSeed':8
}
buffer_style = 2

In [284]:
px = utils.DistanceConverter(page_x_inches, 'inches').mm
py = utils.DistanceConverter(page_y_inches, 'inches').mm
page_format = f'{px}mmx{py}mm'
drawbox = sg.box(border, border, px-border, py-border)

xmin, ymin, xmax, ymax = drawbox.bounds
brad = np.min([gp.get_width(drawbox), gp.get_height(drawbox)])
pg = gp.PerlinGrid(drawbox, **perlin_grid_params)

In [285]:
start_area = drawbox

In [286]:
xcs, ycs = gp.overlay_grid(start_area, xstep=15, ystep=15)
start_pts = [Point(x,y) for x,y in itertools.product(xcs, ycs)]
start_pts = [p for p in start_pts if start_area.contains(p)]

In [287]:
gpolys = []
for p in start_pts:

    pc = ParticleCluster(pos=p, perlin_grid=pg)
    pc.gen_start_pts_gaussian(n_particles=30, xscale=7, yscale=7)
    pc.init_particles(start_bounds=drawbox)
    n_steps = np.random.randint(low=10, high=90, size=len(pc.particles))
    pc.step(n_steps)

    buffer_distances = np.random.uniform(low=0.3, high=1.3) + np.random.uniform(low=0., high=0.7, size=len(pc.lines))
    polys = []
    for line, bd in zip(pc.lines, buffer_distances):
        poly = line.buffer(bd,
            cap_style=buffer_style,
            join_style=buffer_style)
        polys.append(poly)

    P = gp.Poly(so.unary_union(polys))

    stp = ScaleTransPrms(
        d_buffer=np.random.uniform(low=-0.4, high=-0.2),
        d_translate_factor=0.7,
        angles=-240,

    )
    stp.d_buffers += np.random.uniform(-0.03, 0.03, size=stp.d_buffers.shape)
    P.fill_scale_trans(**stp.prms)
    gpolys.append(P)

In [288]:
zorder = np.random.permutation(len(gpolys))

for z, gpoly in zip(zorder, gpolys):
    gpoly.z = z

for gp0, gp1 in itertools.combinations(gpolys, r=2):
    try:
        overlaps = gp0.p.overlaps(gp1.p)
    except:
        gp0.p = gp0.p.buffer(1e-6)
        gp1.p = gp1.p.buffer(1e-6)
        overlaps = gp0.p.overlaps(gp1.p)
    if overlaps:
        if gp0.z > gp1.z:
            gp1.p = occlude(top=gp0.p, bottom=gp1.p)
        elif gp0.z < gp1.z:
            gp0.p = occlude(top=gp1.p, bottom=gp0.p)

ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (11.6192 154.119, 11.657 154.178) and LINESTRING (12.1868 153.85, 11.657 154.178) at 11.657013598218519 154.1780517301664
ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (119.839 42.1077, 119.945 42.0831) and LINESTRING (119.019 42.2985, 119.953 42.0811) at 119.93166093014089 42.086148909921164
ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (119.839 42.1077, 119.945 42.0831) and LINESTRING (119.019 42.2985, 119.953 42.0811) at 119.93166093014089 42.086148909921164
ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (58.868 98.0492, 58.8524 97.9919) and LINESTRING (58.8003 97.8013, 58.8815 98.0985) at 58.865517823595567 98.039935611714156
ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (92.3745 92.2225, 92.3733 92.2225) and LINESTRING (92.4403 92.2244, 92.

In [294]:
gpolys = [p for p in gpolys if p.p.area > 1e-10]

In [301]:
mls = ifills[0]

In [303]:
list(mls)

In [295]:
ifills = []
for p in gpolys:
    ifills.append(p.intersection_fill)

ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (140.388 119.449, 140.462 119.6) and LINESTRING (140.692 119.357, 140.411 119.496) at 140.41115749203914 119.49633764843213
ERROR:shapely.geos:TopologyException: found non-noded intersection between LINESTRING (112.457 56.8814, 113.334 57.0974) and LINESTRING (113.1 57.0614, 113.334 57.0974) at 113.33379101395715 57.097370864469553


In [296]:
splits = utils.random_split(ifills, n_layers=4)
layers = [utils.merge_LineStrings(split) for split in splits]

In [297]:
sk = vsketch.Vsketch()
sk.size(page_format)
sk.scale('1mm')
sk.penWidth('0.25mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2020-11-30T15:52:43.987028 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="-0.3415,668.7832 1.522,670.1553 -0.0041,672.1629 1.2045,673.0817 -1.7863,676.492 0.556,678.5463 2.0218,679.6397 -2.1321,684.9925 -0.8889,685.9572 -2.3704,687.6121 -0.2589,689.5024 2.3798,691.966 7.5579,697.2088 10.152,699.9888 13.0915,702.9164 16.3882,705.6169 19.8761,708.0489 23.7222,710.2268 27.734,711.8162 31.4499,713.0535 35.2412,714.3421 39.067,715.2787 42.454,716.216 49.7598,718.7703 49.4754,719.8375 44.4225,718.8945 40.56,718.2933 36.5815,717.8809 32.5895,717.8177 28.8034,717.9338 25.2544,717.8963 21.8365,717.5042 18.7692,716.8059 15.8702,715.1807 12.8623,713.5025 10.2778,711.2307 7.7209,708.9832 5.7982,706.2587 4.2735,703.8839 -1.0746,707.3176 0.5253,709.8096 2.9612,713.261 6.0818,716.0041 9.1747,718.7229 12.768,720.7276 16.4626,722.7988 17.8572,723.117 17.8572,723.1163 20.7657,723.7785 24.8576,724.2479 28.8673,724.2903 32.6367,724.1747 36.2028,724.2311 39.7431,724.5982 43.3496,725.1595 50.7427,726.5416 46.5399,727.5516 44.426,727.6787 40.438,728.174 36.3803,729.0355 32.6334,730.4178 29.0961,731.6799 27.3097,732.309 26.2393,726.8556 26.0264,726.8974 25.978,726.6507 22.887,727.2573 18.1974,728.6944 17.9643,724.8718 15.1134,725.0467 11.4523,725.2241 7.8897,725.2976 4.4754,725.2026 1.8256,724.9162 0.9506,733.0112 -1.3381,733.4108 0.2638,742.5857 7.455,741.3327 7.5979,741.7601 1.5307,744.8635 -1.0372,746.0556 2.1511,752.9235 0.0314,754.6337 -2.2193,756.3461 3.192,763.4585 5.5441,761.6689 9.423,758.5392 6.7136,765.1877 5.4918,769.5702 5.1159,774.1748 5.3771,778.4242 5.8185,782.4833 6.5654,786.5417 7.603,790.6705 9.1461,794.6282 10.8414,798.3031 12.6666,801.8252 14.6656,805.4265 17.1887,809.0138 20.2367,812.3025 26.7888,817.5818 30.7256,819.6521 33.5379,820.8848 35.6428,816.0826 38.7774,817.6289 42.0228,819.2966 44.4695,820.6639 46.998,816.1391 48.5552,817.33 52.1074,819.426 54.6753,820.867 54.6947,820.8323 54.8312,820.9089 56.5416,817.8612 58.9741,819.418 61.4149,820.9745 63.4746,817.7447 66.6751,820.0888 68.4433,821.8676 69.6942,820.6241 70.445,821.6525 72.5637,820.1056 72.8951,820.5594 75.4535,818.6916 76.1435,820.1351 77.1643,819.6472 77.5258,820.6971 83.3722,818.6842 83.5326,819.762 94.1205,818.1861 93.1835,811.8915 93.0711,808.4884 93.0434,804.9876 93.2921,801.4912 93.6351,797.8754 94.0764,794.3944 94.7178,791.1587 95.6571,788.1822 97.01,785.3186 98.5747,782.6739 100.5511,780.3508 102.8064,778.1881 105.3681,776.3533 107.9418,774.8457 110.8142,773.8792 114.1367,773.0279 117.5962,772.3485 120.3525,771.9151 118.6897,761.3405 115.7327,761.8055 111.7748,762.5828 107.7748,763.6077 103.4828,765.0518 99.5341,767.3649 95.9504,769.9316 92.7499,773.0008 89.8282,776.4351 87.5438,780.2961 85.6677,784.2672 84.3322,788.4993 82.9522,795.4616 82.0306,791.1733 81.8785,788.0933 82.0883,784.9478 82.6865,782.0197 83.8539,779.1202 85.3678,776.0867 87.0894,773.2055 

In [304]:
savepath = '/mnt/c/code/side/plotter_images/oned_outputs/0084_perlin_flow_erode_frays_occlude.svg'

sk.save(savepath)

vpype_commands = 'linesimplify --tolerance 0.05mm linemerge --tolerance 0.1mm reloop linesort'
vpype_str = f'vpype read -q 0.05mm {savepath} {vpype_commands} write --page-format {page_format} {savepath}'

os.system(vpype_str)

512